In [1]:
#Librerias necesarias para implementacion de algoritmo genetico
from __future__ import print_function

from evolver import Evolver

from tqdm import tqdm

import logging

import sys


# Aplicacion del Modelo
Aqui se aplica directamente el modelo descrito implementando el algoritmo genetico

In [2]:
#Librerias necesarias para trabajar con datasets
import pandas as pd
import numpy as np
from sklearn import linear_model, model_selection

#Librerias necesarias para aplicar redes neuronales
import tensorflow as tf
pd.set_option('display.max_columns', None)
df= pd.read_csv("Historial_Alumnos.csv", sep=",",index_col=False)
df.head()

id_anony Cod.Car.Sec  Cod.Car.Sec Codificado  Materia_1  \
0      2838  MCT-PLS13                     28.0  CALCULO 1   
1      4037  MCT-PLS13                     28.0  CALCULO 1   
2      4061  MCT-PLS13                     28.0  CALCULO 1   
3      4062  MCT-PLS13                     28.0  CALCULO 1   
4      4065  MCT-PLS13                     28.0  CALCULO 1   

   Materia_1 codificada  Anho_F_1  ciclo_F_1  Recursante_1  P1_F_1  P2_F_1  \
0                  33.0    2013.0        2.0           1.0     0.0    17.0   
1                  33.0    2015.0        2.0           1.0    16.0    19.0   
2                  33.0    2015.0        2.0           1.0    14.0    27.0   
3                  33.0    2015.0        2.0           1.0     5.0    24.0   
4                  33.0    2015.0        2.0           1.0    19.0    30.0   

   T_F_1  NotaFinal_1  Materia_1 Nota=1  Materia_1 Nota=2  Materia_1 Nota=3  \
0    8.0          2.0               0.0               1.0               0.0   
1    8.0          5.0               0.0               0.0               0.0   
2    8.0          3.0               0.0               0.0               1.0   
3    6.0          2.0               0.0               1.0               0.0   
4    9.0          5.0               0.0               0.0               0.0   

   Materia_1 Nota=4  Materia_1 Nota=5  Abandono la Materia 1  Materia_2  \
0               0.0               0.0                    1.0  CALCULO 2   
1               0.0               1.0                    0.0  CALCULO 2   
2               0.0               0.0                    0.0  CALCULO 2   
3               0.0               0.0                    0.0  CALCULO 2   
4               0.0               1.0                    0.0  CALCULO 2   

   Materia_2 codificada  Anho_F_2  ciclo_F_2  Recursante_2  P1_F_2  P2_F_2  \
0                  34.0    2014.0        1.0           1.0    11.0    16.0   
1                  34.0    2016.0        1.0           1.0    22.0    31.0   
2                  34.0    2016.0        1.0           1.0    13.0    23.0   
3                  34.0    2016.0        1.0           1.0    21.0    19.0   
4                  34.0    2016.0        1.0           1.0    24.0    29.0   

   T_F_2  NotaFinal_2  Materia_2 Nota=1  Materia_2 Nota=2  Materia_2 Nota=3  \
0    8.0          2.0               0.0               1.0               0.0   
1    7.0          5.0               0.0               0.0               0.0   
2    5.0          2.0               0.0               1.0               0.0   
3    5.0          2.0               0.0               1.0               0.0   
4    9.0          5.0               0.0               0.0               0.0   

   Materia_2 Nota=4  Materia_2 Nota=5  Abandono la Materia 2  Materia_3  \
0               0.0               0.0                    0.0  CALCULO 3   
1               0.0               1.0                    0.0  CALCULO 3   
2               0.0               0.0                    0.0  CALCULO 3   
3               0.0               0.0                    0.0  CALCULO 3   
4               0.0               1.0                    0.0  CALCULO 3   

   Materia_3 codificada  Anho_F_3  ciclo_F_3  Recursante_3  P1_F_3  P2_F_3  \
0                  35.0    2016.0        2.0           1.0    10.0     7.0   
1                  35.0    2016.0        2.0           1.0     6.0     9.0   
2                  35.0    2016.0        2.0           1.0    17.0    10.0   
3                  35.0    2016.0        2.0           1.0     5.0    18.0   
4                  35.0    2016.0        2.0           1.0    22.0    20.0   

   T_F_3  NotaFinal_3  Materia_3 Nota=1  Materia_3 Nota=2  Materia_3 Nota=3  \
0    2.0          2.0               0.0               1.0               0.0   
1    8.0          4.0               0.0               0.0               0.0   
2    8.0          2.0               0.0               1.0               0.0   
3    6.0          2.0               0.0               1

Antes que nada, es necesario preparar los datos que la red neuronal solicita para poder procesar la opcion mas viable para nuestro analisis

In [3]:
data=df[['Materia_1 codificada','Anho_F_1','ciclo_F_1','Recursante_1','P1_F_1','P2_F_1','T_F_1','NotaFinal_1','Abandono la Materia 1','Materia_2 codificada','Anho_F_2','ciclo_F_2','Recursante_2','P1_F_2','P2_F_2','T_F_2','NotaFinal_2','Abandono la Materia 2']]

[filas,columnas]=data.shape
labels=df[['Materia_3 Nota=4']]

#Como labels figura como string, es necesario cambiarlos a valores enteros
data = np.array(data)
labels = np.array(labels)
labels=np.ravel(labels)

#Verificamos las dimensiones de data y labels
display(np.shape(labels))
display(np.shape(data))

(56,)

(56, 18)

Los datos que el algoritmo genetico solicita a lo largo de su procesamiento son data, labels y columnas. Para facilitar dichos datos del notebook al algoritmo genetico, se emplea la libreria pickle

In [4]:
from pickle import dump,load
dump(data, open('data.pkl', 'wb'))
dump(labels, open('labels.pkl', 'wb'))
dump(columnas, open('columnas.pkl', 'wb'))

Una vez definidos apropiadamente estos parametros, se procede a realizar el procesamiento con el algoritmo genetico

In [5]:
import main as ge
lista=ge.main()

07/07/2021 10:25:25 AM - INFO - ***generate(generations, population, all_possible_genes, dataset)***
07/07/2021 10:25:25 AM - INFO - ***Now in generation 1 of 50***
07/07/2021 10:25:25 AM - INFO - --------------------------------------------------------------------------------
07/07/2021 10:25:25 AM - INFO - {'nb_layers': 1, 'activation': 'sigmoid', 'optimizer': 'adamax', 'nb_neurons': [32, 16, 32, 64, 64, 16]}
07/07/2021 10:25:25 AM - INFO - Acc: 0.00%
07/07/2021 10:25:25 AM - INFO - UniID: 1
07/07/2021 10:25:25 AM - INFO - Mom and Dad: 0 0
07/07/2021 10:25:25 AM - INFO - Gen: 1
07/07/2021 10:25:25 AM - INFO - Hash: 24d661a2ef8ef331c78a8a6158586aa4
07/07/2021 10:25:25 AM - INFO - {'nb_layers': 2, 'activation': 'softmax', 'optimizer': 'adamax', 'nb_neurons': [64, 16, 16, 16, 16, 32]}
07/07/2021 10:25:25 AM - INFO - Acc: 0.00%
07/07/2021 10:25:25 AM - INFO - UniID: 2
07/07/2021 10:25:25 AM - INFO - Mom and Dad: 0 0
07/07/2021 10:25:25 AM - INFO - Gen: 1
07/07/2021 10:25:25 AM - INFO - H

07/07/2021 10:25:25 AM - INFO - Hash: eab0cea3fd72ecdb9989e6ccb3ad9a56
07/07/2021 10:25:25 AM - INFO - {'nb_layers': 4, 'activation': 'softmax', 'optimizer': 'adam', 'nb_neurons': [16, 64, 16, 128, 16, 16]}
07/07/2021 10:25:25 AM - INFO - Acc: 0.00%
07/07/2021 10:25:25 AM - INFO - UniID: 22
07/07/2021 10:25:25 AM - INFO - Mom and Dad: 0 0
07/07/2021 10:25:25 AM - INFO - Gen: 1
07/07/2021 10:25:25 AM - INFO - Hash: 72433880b8618afdf85741373da6ab2e
07/07/2021 10:25:25 AM - INFO - {'nb_layers': 3, 'activation': 'relu', 'optimizer': 'adam', 'nb_neurons': [16, 128, 16, 32, 32, 64]}
07/07/2021 10:25:25 AM - INFO - Acc: 0.00%
07/07/2021 10:25:25 AM - INFO - UniID: 23
07/07/2021 10:25:25 AM - INFO - Mom and Dad: 0 0
07/07/2021 10:25:25 AM - INFO - Gen: 1
07/07/2021 10:25:25 AM - INFO - Hash: ecaf337b4d7b07ddc5826e66e6ea0ce1
07/07/2021 10:25:25 AM - INFO - {'nb_layers': 5, 'activation': 'relu', 'optimizer': 'adam', 'nb_neurons': [64, 64, 64, 64, 32, 32]}
07/07/2021 10:25:25 AM - INFO - Acc: 0.0

***Dataset: dataset
***Evolving for 50 generations with population size = 30***
(44,)
(44, 18)
(44, 2)
(44, 18)
(44, 18)
(44, 2)
Epoch 1/50
1/1 [==============================] - 0s 129ms/step - loss: 0.6739 - accuracy: 0.5455 - val_loss: 0.6877 - val_accuracy: 0.4167
Epoch 2/50
1/1 [==============================] - 0s 14ms/step - loss: 0.7142 - accuracy: 0.5227 - val_loss: 0.6717 - val_accuracy: 0.6667
Epoch 3/50
1/1 [==============================] - 0s 15ms/step - loss: 0.7852 - accuracy: 0.3636 - val_loss: 0.6568 - val_accuracy: 0.8333


  3%|▎         | 1/30 [00:00<00:28,  1.01it/s]07/07/2021 10:25:26 AM - INFO - Getting Keras datasets
07/07/2021 10:25:26 AM - INFO - Compling Keras model
07/07/2021 10:25:26 AM - INFO - Architecture:[64, 16, 16, 16, 16, 32],softmax,adamax,2


Test loss: 0.6567873358726501
Test accuracy: 0.8333333134651184

 Modelo mas eficiente creado 

(44,)
(44, 18)
(44, 2)
(44, 18)
(44, 18)
(44, 2)
Epoch 1/50
1/1 [==============================] - 0s 124ms/step - loss: 0.7591 - accuracy: 0.1136 - val_loss: 0.7451 - val_accuracy: 0.1667
Epoch 2/50
1/1 [==============================] - 0s 11ms/step - loss: 0.7498 - accuracy: 0.1136 - val_loss: 0.7434 - val_accuracy: 0.1667
Epoch 3/50
1/1 [==============================] - 0s 12ms/step - loss: 0.7473 - accuracy: 0.1136 - val_loss: 0.7417 - val_accuracy: 0.1667
Test loss: 0.7417082190513611
Test accuracy: 0.1666666716337204


...

Test loss: 0.5949676632881165
Test accuracy: 0.8333333134651184
(44,)
(44, 18)
(44, 2)
(44, 18)
(44, 18)
(44, 2)
Epoch 1/50
1/1 [==============================] - 0s 132ms/step - loss: 0.7462 - accuracy: 0.1136 - val_loss: 0.7149 - val_accuracy: 0.1667
Epoch 2/50
1/1 [==============================] - 0s 11ms/step - loss: 0.7211 - accuracy: 0.1818 - val_loss: 0.7039 - val_accuracy: 0.1667
Epoch 3/50
1/1 [==============================] - 0s 13ms/step - loss: 0.7107 - accuracy: 0.3409 - val_loss: 0.6947 - val_accuracy: 0.5000
Test loss: 0.6946517825126648
Test accuracy: 0.5


 98%|█████████▊| 51/52 [00:39<00:00,  1.08it/s]07/07/2021 10:50:34 AM - INFO - Getting Keras datasets
07/07/2021 10:50:34 AM - INFO - Compling Keras model
07/07/2021 10:50:34 AM - INFO - Architecture:[32, 16, 32, 128, 64, 64],sigmoid,adamax,2


(44,)
(44, 18)
(44, 2)
(44, 18)
(44, 18)
(44, 2)
Epoch 1/50
1/1 [==============================] - 0s 101ms/step - loss: 0.4930 - accuracy: 0.8409 - val_loss: 0.4656 - val_accuracy: 0.8333
Epoch 2/50
1/1 [==============================] - 0s 9ms/step - loss: 0.4183 - accuracy: 0.8864 - val_loss: 0.4628 - val_accuracy: 0.8333
Epoch 3/50
1/1 [==============================] - 0s 10ms/step - loss: 0.4101 - accuracy: 0.9091 - val_loss: 0.4604 - val_accuracy: 0.8333


100%|██████████| 52/52 [00:39<00:00,  1.30it/s]
07/07/2021 10:50:35 AM - INFO - Generation average: 69.71%
07/07/2021 10:50:35 AM - INFO - --------------------------------------------------------------------------------
07/07/2021 10:50:35 AM - INFO - --------------------------------------------------------------------------------
07/07/2021 10:50:35 AM - INFO - {'activation': 'relu', 'nb_layers': 2, 'optimizer': 'adamax', 'nb_neurons': [32, 16, 32, 64, 64, 64]}
07/07/2021 10:50:35 AM - INFO - Acc: 91.67%
07/07/2021 10:50:35 AM - INFO - UniID: 222
07/07/2021 10:50:35 AM - INFO - Mom and Dad: 193 199
07/07/2021 10:50:35 AM - INFO - Gen: 9
07/07/2021 10:50:35 AM - INFO - Hash: 153a9786ba104f68a2fa1fa0c023a106
07/07/2021 10:50:35 AM - INFO - {'activation': 'relu', 'nb_layers': 1, 'optimizer': 'adamax', 'nb_neurons': [32, 16, 32, 32, 64, 128]}
07/07/2021 10:50:35 AM - INFO - Acc: 91.67%
07/07/2021 10:50:35 AM - INFO - UniID: 240
07/07/2021 10:50:35 AM - INFO - Mom and Dad: 8 110
07/07/2021

Test loss: 0.46035775542259216
Test accuracy: 0.8333333134651184
